# Hyperparameter Tuning

Using Scikit-Learn’s RandomizedSearchCV method, we can define a grid of hyperparameter ranges, and randomly sample from the grid, performing K-Fold CV with each combination of values.

In [1]:
import numpy as np
import pandas as pd
from pprint import pprint
from sklearn.model_selection import GridSearchCV
from sklearn.ensemble import ExtraTreesRegressor
from sklearn.model_selection import train_test_split
from sklearn.model_selection import RandomizedSearchCV
from sklearn.metrics import mean_absolute_error, mean_squared_error

In [2]:
base_regressor = ExtraTreesRegressor()

print('Parameters currently in use:\n')
pprint(base_regressor.get_params())

Parameters currently in use:

{'bootstrap': False,
 'ccp_alpha': 0.0,
 'criterion': 'squared_error',
 'max_depth': None,
 'max_features': 1.0,
 'max_leaf_nodes': None,
 'max_samples': None,
 'min_impurity_decrease': 0.0,
 'min_samples_leaf': 1,
 'min_samples_split': 2,
 'min_weight_fraction_leaf': 0.0,
 'n_estimators': 100,
 'n_jobs': None,
 'oob_score': False,
 'random_state': None,
 'verbose': 0,
 'warm_start': False}


We will try adjusting the following set of hyperparameters:
* n_estimators = number of trees in the foreset
* criterion = the function to measure the quality of a split
* max_depth = max number of levels in each decision tree
* min_samples_leaf = min number of data points allowed in a leaf node
* min_samples_split = min number of data points placed in a node before the node is split
* max_features = max number of features considered for splitting a node
* bootstrap = method for sampling data points (with or without replacement)

In [3]:
# Number of trees in random forest
n_estimators = [int(x) for x in np.linspace(start = 200, stop = 2000, num = 10)]

# The function to measure the quality of a split
criteria = ["squared_error", "absolute_error", "friedman_mse", "poisson"]

# Number of features to consider at every split
max_features = ['sqrt', 'log2']

# Maximum number of levels in tree
max_depth = [int(x) for x in np.linspace(10, 110, num = 11)]
max_depth.append(None)

# Minimum number of samples required to split a node
min_samples_split = [2, 5, 10]

# Minimum number of samples required at each leaf node
min_samples_leaf = [1, 2, 4]

# Method of selecting samples for training each tree
bootstrap = [True, False]

# Create the random grid
random_grid = {'n_estimators': n_estimators,
               'max_features': max_features,
               'max_depth': max_depth,
               'criterion': criteria,
               'min_samples_split': min_samples_split,
               'min_samples_leaf': min_samples_leaf,
               'bootstrap': bootstrap}
pprint(random_grid)

{'bootstrap': [True, False],
 'criterion': ['squared_error', 'absolute_error', 'friedman_mse', 'poisson'],
 'max_depth': [10, 20, 30, 40, 50, 60, 70, 80, 90, 100, 110, None],
 'max_features': ['sqrt', 'log2'],
 'min_samples_leaf': [1, 2, 4],
 'min_samples_split': [2, 5, 10],
 'n_estimators': [200, 400, 600, 800, 1000, 1200, 1400, 1600, 1800, 2000]}


In [4]:
base_path = '/kaggle/input/self-reported-qol/20230625-processed-'

df_physical      = pd.read_csv(base_path + 'physical-qol.csv')
df_psychological = pd.read_csv(base_path + 'psychological-qol.csv')

df_physical.drop('id', axis=1, inplace=True)         # id
df_physical.drop('day', axis=1, inplace=True)        # day
df_psychological.drop('id', axis=1, inplace=True)    # id
df_psychological.drop('day', axis=1, inplace=True)   # day

phy_all_tmp = df_physical.copy()
phy_init_set_tmp = phy_all_tmp.query("group in ('Initial Set')").copy()
phy_ufpi_ufc_tmp = phy_all_tmp.query("group in ('UFPI', 'UFC')").copy()

psy_all_tmp = df_psychological.copy()
psy_init_set_tmp = psy_all_tmp.query("group in ('Initial Set')").copy()
psy_ufpi_ufc_tmp = psy_all_tmp.query("group in ('UFPI', 'UFC')").copy()

phy_all_tmp.drop("group", axis=1, inplace=True)
phy_init_set_tmp.drop("group", axis=1, inplace=True)
phy_ufpi_ufc_tmp.drop("group", axis=1, inplace=True)

psy_all_tmp.drop("group", axis=1, inplace=True)
psy_init_set_tmp.drop("group", axis=1, inplace=True)
psy_ufpi_ufc_tmp.drop("group", axis=1, inplace=True)

# Separating predictors from the values to be predicted.
phy_all           = phy_all_tmp.drop("phy_ref_score", axis=1)
phy_all_pred      = phy_all_tmp["phy_ref_score"].copy()
phy_init_set      = phy_init_set_tmp.drop("phy_ref_score", axis=1)
phy_init_set_pred = phy_init_set_tmp["phy_ref_score"].copy()
phy_ufpi_ufc      = phy_ufpi_ufc_tmp.drop("phy_ref_score", axis=1)
phy_ufpi_ufc_pred = phy_ufpi_ufc_tmp["phy_ref_score"].copy()

psy_all           = psy_all_tmp.drop("psy_ref_score", axis=1)
psy_all_pred      = psy_all_tmp["psy_ref_score"].copy()
psy_init_set      = psy_init_set_tmp.drop("psy_ref_score", axis=1)
psy_init_set_pred = psy_init_set_tmp["psy_ref_score"].copy()
psy_ufpi_ufc      = psy_ufpi_ufc_tmp.drop("psy_ref_score", axis=1)
psy_ufpi_ufc_pred = psy_ufpi_ufc_tmp["psy_ref_score"].copy()

In [5]:
def getDataset(domain_group):
    return {
        'phy_all': (phy_all, phy_all_pred),
        'psy_all': (psy_all, psy_all_pred),
        
        'phy_init_set': (phy_init_set, phy_init_set_pred),
        'psy_init_set': (psy_init_set, psy_init_set_pred),
        
        'phy_ufpi_ufc': (phy_ufpi_ufc, phy_ufpi_ufc_pred),
        'psy_ufpi_ufc': (psy_ufpi_ufc, psy_ufpi_ufc_pred),
    }[domain_group] 

In [6]:
features, labels = getDataset('phy_all')
train_features, test_features, train_labels, test_labels = train_test_split(features, labels, test_size = 0.3, random_state = 42)

In [7]:
print('Training Features Shape:', train_features.shape)
print('Training Labels Shape:',   train_labels.shape)
print('Testing Features Shape:',  test_features.shape)
print('Testing Labels Shape:',    test_labels.shape)

Training Features Shape: (961, 86)
Training Labels Shape: (961,)
Testing Features Shape: (412, 86)
Testing Labels Shape: (412,)


In [8]:
iterations = 2
cv_number = 2

In [9]:
rscv = RandomizedSearchCV(estimator = base_regressor, param_distributions = random_grid, n_iter = iterations, cv = cv_number, verbose=2, random_state=42, n_jobs = -1)
rscv.fit(train_features, train_labels)

Fitting 2 folds for each of 2 candidates, totalling 4 fits


RandomizedSearchCV(cv=2, estimator=ExtraTreesRegressor(), n_iter=2, n_jobs=-1,
                   param_distributions={'bootstrap': [True, False],
                                        'criterion': ['squared_error',
                                                      'absolute_error',
                                                      'friedman_mse',
                                                      'poisson'],
                                        'max_depth': [10, 20, 30, 40, 50, 60,
                                                      70, 80, 90, 100, 110,
                                                      None],
                                        'max_features': ['sqrt', 'log2'],
                                        'min_samples_leaf': [1, 2, 4],
                                        'min_samples_split': [2, 5, 10],
                                        'n_estimators': [200, 400, 600, 800,
                                                         1000, 1200, 1400, 1600,
                                                         1800, 2000]},
                   random_state=42, verbose=2)

In [10]:
rscv.best_params_

{'n_estimators': 1200,
 'min_samples_split': 5,
 'min_samples_leaf': 2,
 'max_features': 'log2',
 'max_depth': 40,
 'criterion': 'poisson',
 'bootstrap': False}

In [11]:
def evaluate_mae_rmse(name, model, test_features, test_labels):
    predictions = model.predict(test_features)
    mae = mean_absolute_error(test_labels, predictions)
    rmse = mean_squared_error(test_labels, predictions, squared=False)
    print('Model Performance of', name, 'MAE = {:0.4f} RMSE = {:0.4f}'.format(mae, rmse))
    return mae, rmse

def check_improvement(base_model, new_model):
    b_mae, b_rmse = evaluate_mae_rmse('baseline', base_model, test_features, test_labels)
    n_mae, n_rmse = evaluate_mae_rmse('improved', new_model, test_features, test_labels)
    print('Improvement of {:0.2f}% in MAE'.format( 100 * (n_mae - b_mae) / b_mae))
    print('Improvement of {:0.2f}% in RMSE'.format( 100 * (n_rmse - b_rmse) / b_rmse))

In [12]:
base_regressor.fit(train_features, train_labels)
evaluate_mae_rmse('Baseline', base_regressor, test_features, test_labels)

Model Performance of Baseline MAE = 4.1984 RMSE = 6.0683


(4.198373786407767, 6.068314072261888)

In [13]:
best_random = rscv.best_estimator_
evaluate_mae_rmse('Improved by RandomizedSearchCV', best_random, test_features, test_labels)

Model Performance of Improved by RandomizedSearchCV MAE = 5.3404 RMSE = 7.1778


(5.340433818722427, 7.177819329697166)

In [14]:
check_improvement(base_regressor, best_random)

Model Performance of baseline MAE = 4.1984 RMSE = 6.0683
Model Performance of improved MAE = 5.3404 RMSE = 7.1778
Improvement of 27.20% in MAE
Improvement of 18.28% in RMSE


In [15]:
# Create the parameter grid based on the results of random search 
param_grid = {
    'bootstrap': [True, False],
    'warm_start': [True, False],
    'min_samples_leaf': [3, 4, 5],
    'min_samples_split': [8, 10, 12],
    'max_depth': [80, 90, 100, 110],
    'max_features': ['auto','sqrt','log2'],
    'criterion': ["squared_error", "absolute_error", "friedman_mse", "poisson"],
    'n_estimators': [100, 300, 500, 1000, 1500, 2000]
}

grid_search = GridSearchCV(estimator = base_regressor, param_grid = param_grid, cv = cv_number, n_jobs = -1, verbose = 2)

In [16]:
grid_search.fit(train_features, train_labels)
grid_search.best_params_

Fitting 2 folds for each of 10368 candidates, totalling 20736 fits


/opt/conda/lib/python3.10/site-packages/sklearn/ensemble/_forest.py:413: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_features=1.0` or remove this parameter as it is also the default value for RandomForestRegressors and ExtraTreesRegressors.
  warn(
/opt/conda/lib/python3.10/site-packages/sklearn/ensemble/_forest.py:413: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_features=1.0` or remove this parameter as it is also the default value for RandomForestRegressors and ExtraTreesRegressors.
  warn(
/opt/conda/lib/python3.10/site-packages/sklearn/ensemble/_forest.py:413: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_features=1.0` or remove this parameter as it is also the default value for RandomForestRegressors

[CV] END bootstrap=False, criterion=poisson, max_depth=40, max_features=log2, min_samples_leaf=2, min_samples_split=5, n_estimators=1200; total time=   2.1s
[CV] END bootstrap=True, criterion=squared_error, max_depth=80, max_features=auto, min_samples_leaf=3, min_samples_split=8, n_estimators=100, warm_start=False; total time=   0.5s
[CV] END bootstrap=True, criterion=squared_error, max_depth=80, max_features=auto, min_samples_leaf=3, min_samples_split=8, n_estimators=300, warm_start=True; total time=   1.4s
[CV] END bootstrap=True, criterion=squared_error, max_depth=80, max_features=auto, min_samples_leaf=3, min_samples_split=8, n_estimators=500, warm_start=True; total time=   2.6s
[CV] END bootstrap=True, criterion=squared_error, max_depth=80, max_features=auto, min_samples_leaf=3, min_samples_split=8, n_estimators=1000, warm_start=True; total time=   4.4s
[CV] END bootstrap=True, criterion=squared_error, max_depth=80, max_features=auto, min_samples_leaf=3, min_samples_split=8, n_est

/opt/conda/lib/python3.10/site-packages/sklearn/ensemble/_forest.py:413: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_features=1.0` or remove this parameter as it is also the default value for RandomForestRegressors and ExtraTreesRegressors.
  warn(
/opt/conda/lib/python3.10/site-packages/sklearn/ensemble/_forest.py:413: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_features=1.0` or remove this parameter as it is also the default value for RandomForestRegressors and ExtraTreesRegressors.
  warn(


[CV] END bootstrap=False, criterion=poisson, max_depth=40, max_features=log2, min_samples_leaf=2, min_samples_split=5, n_estimators=1200; total time=   2.2s
[CV] END bootstrap=True, criterion=squared_error, max_depth=80, max_features=auto, min_samples_leaf=3, min_samples_split=8, n_estimators=100, warm_start=False; total time=   0.5s
[CV] END bootstrap=True, criterion=squared_error, max_depth=80, max_features=auto, min_samples_leaf=3, min_samples_split=8, n_estimators=300, warm_start=False; total time=   1.5s
[CV] END bootstrap=True, criterion=squared_error, max_depth=80, max_features=auto, min_samples_leaf=3, min_samples_split=8, n_estimators=500, warm_start=False; total time=   2.7s
[CV] END bootstrap=True, criterion=squared_error, max_depth=80, max_features=auto, min_samples_leaf=3, min_samples_split=8, n_estimators=1000, warm_start=True; total time=   4.5s
[CV] END bootstrap=True, criterion=squared_error, max_depth=80, max_features=auto, min_samples_leaf=3, min_samples_split=8, n_e

...

[CV] END bootstrap=False, criterion=poisson, max_depth=100, max_features=log2, min_samples_leaf=5, min_samples_split=12, n_estimators=1500, warm_start=True; total time=   3.1s
[CV] END bootstrap=False, criterion=poisson, max_depth=100, max_features=log2, min_samples_leaf=5, min_samples_split=12, n_estimators=2000, warm_start=True; total time=   4.1s
[CV] END bootstrap=False, criterion=poisson, max_depth=110, max_features=auto, min_samples_leaf=3, min_samples_split=8, n_estimators=100, warm_start=True; total time=   0.6s
[CV] END bootstrap=False, criterion=poisson, max_depth=110, max_features=auto, min_samples_leaf=3, min_samples_split=8, n_estimators=300, warm_start=True; total time=   1.7s
[CV] END bootstrap=False, criterion=poisson, max_depth=110, max_features=auto, min_samples_leaf=3, min_samples_split=8, n_estimators=500, warm_start=True; total time=   2.8s
[CV] END bootstrap=False, criterion=poisson, max_depth=110, max_features=auto, min_samples_leaf=3, min_samples_split=8, n_esti

/opt/conda/lib/python3.10/site-packages/sklearn/ensemble/_forest.py:413: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_features=1.0` or remove this parameter as it is also the default value for RandomForestRegressors and ExtraTreesRegressors.
  warn(
/opt/conda/lib/python3.10/site-packages/sklearn/ensemble/_forest.py:413: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_features=1.0` or remove this parameter as it is also the default value for RandomForestRegressors and ExtraTreesRegressors.
  warn(
/opt/conda/lib/python3.10/site-packages/sklearn/ensemble/_forest.py:413: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_features=1.0` or remove this parameter as it is also the default value for RandomForestRegressors

[CV] END bootstrap=False, criterion=poisson, max_depth=110, max_features=auto, min_samples_leaf=3, min_samples_split=10, n_estimators=300, warm_start=False; total time=   1.6s
[CV] END bootstrap=False, criterion=poisson, max_depth=110, max_features=auto, min_samples_leaf=3, min_samples_split=10, n_estimators=500, warm_start=False; total time=   2.6s
[CV] END bootstrap=False, criterion=poisson, max_depth=110, max_features=auto, min_samples_leaf=3, min_samples_split=10, n_estimators=1000, warm_start=False; total time=   5.4s
[CV] END bootstrap=False, criterion=poisson, max_depth=110, max_features=auto, min_samples_leaf=3, min_samples_split=10, n_estimators=1500, warm_start=True; total time=   8.6s
[CV] END bootstrap=False, criterion=poisson, max_depth=110, max_features=auto, min_samples_leaf=3, min_samples_split=10, n_estimators=2000, warm_start=False; total time=  10.6s
[CV] END bootstrap=False, criterion=poisson, max_depth=110, max_features=auto, min_samples_leaf=3, min_samples_split=1

/opt/conda/lib/python3.10/site-packages/sklearn/ensemble/_forest.py:413: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_features=1.0` or remove this parameter as it is also the default value for RandomForestRegressors and ExtraTreesRegressors.
  warn(


{'bootstrap': False,
 'criterion': 'friedman_mse',
 'max_depth': 110,
 'max_features': 'auto',
 'min_samples_leaf': 3,
 'min_samples_split': 8,
 'n_estimators': 100,
 'warm_start': False}

In [17]:
best_grid = grid_search.best_estimator_

In [18]:
check_improvement(base_regressor, best_random)

Model Performance of baseline MAE = 4.1984 RMSE = 6.0683
Model Performance of improved MAE = 5.3404 RMSE = 7.1778
Improvement of 27.20% in MAE
Improvement of 18.28% in RMSE


In [19]:
check_improvement(base_regressor, best_grid)

Model Performance of baseline MAE = 4.1984 RMSE = 6.0683
Model Performance of improved MAE = 4.3818 RMSE = 6.1752
Improvement of 4.37% in MAE
Improvement of 1.76% in RMSE


In [20]:
check_improvement(best_random, best_grid)

Model Performance of baseline MAE = 5.3404 RMSE = 7.1778
Model Performance of improved MAE = 4.3818 RMSE = 6.1752
Improvement of -17.95% in MAE
Improvement of -13.97% in RMSE


In [21]:
feats = {} # a dict to hold feature_name: feature_importance
for feature, importance in zip(features.columns, best_grid.feature_importances_):
    feats[feature] = importance #add the name/value pair 

In [22]:
importances = pd.DataFrame.from_dict(feats, orient='index').rename(columns={0: 'Gini-importance'})
importances.sort_values(by='Gini-importance', inplace=True, ascending=False)
importances

Gini-importance
height                     0.165982
income                     0.145946
weight                     0.073070
awakesleep                 0.047376
profession_student         0.041125
...                             ...
running(treadmill)         0.000000
residence                  0.000000
dating                     0.000000
house                      0.000000
beauty                     0.000000

[86 rows x 1 columns]

In [23]:
from sklearn.tree import export_graphviz

# Write the decision tree as a dot file
visual_tree = best_grid.estimators_[12]
export_graphviz(visual_tree, out_file = 'best_tree.dot', feature_names = features.columns, 
                precision = 2, filled = True, rounded = True, max_depth = None)

In [24]:
import pydot

# Import the dot file to a graph and then convert to a png
(graph, ) = pydot.graph_from_dot_file('best_tree.dot')
graph.write_png('best_tree.png')